<a href="https://colab.research.google.com/github/chengjin-hub/2D-image-of-rock-sample-in-CT-/blob/main/zhujaingsudu3D.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from scipy.spatial import cKDTree

# 1. 读取数据 (请确保文件名匹配)
file_path = 'grouting_final.csv.xlsx - 表格数据 (2).csv'
df = pd.read_csv(file_path)

# 2. 数据预处理
# 将时间转换为秒
df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S')
min_time = df['Time_Obj'].min()
df['Time_Sec'] = (df['Time_Obj'] - min_time).dt.total_seconds()

# 按时间排序
df = df.sort_values('Time_Sec').reset_index(drop=True)

# 3. 计算 3D 速率 (Velocity)
velocities = []
coords = df[['X_cm', 'Y_cm', 'Z_cm']].values
times = df['Time_Sec'].values

for i in range(len(df)):
    current_pos = coords[i]
    current_time = times[i]

    # 找到所有到达时间早于当前点的点
    earlier_mask = times < current_time

    if not np.any(earlier_mask):
        velocities.append(0) # 起始点
        continue

    earlier_coords = coords[earlier_mask]
    earlier_times = times[earlier_mask]

    # 计算到所有已知点的距离
    dists = np.linalg.norm(earlier_coords - current_pos, axis=1)

    # 找到最近的前驱点
    min_dist_idx = np.argmin(dists)
    min_dist = dists[min_dist_idx]
    time_diff = current_time - earlier_times[min_dist_idx]

    # 计算速率 (cm/s)
    if time_diff > 0:
        v = min_dist / time_diff
    else:
        v = 0
    velocities.append(v)

df['Velocity_cm_s'] = velocities

# 4. 生成 3D 交互式图表
fig = go.Figure(data=[go.Scatter3d(
    x=df['X_cm'],
    y=df['Y_cm'],
    z=df['Z_cm'],
    mode='markers',
    marker=dict(
        size=5,
        color=df['Velocity_cm_s'],  # 颜色对应速率
        colorscale='Jet',           # 颜色表
        opacity=0.8,
        colorbar=dict(title="速率 (cm/s)")
    ),
    text=[f"时间: {t}<br>速率: {v:.2f} cm/s" for t, v in zip(df['Arrival_Time_s'], df['Velocity_cm_s'])],
    hoverinfo='text'
)])

fig.update_layout(
    title="3D 注浆扩散速率场 (颜色代表流速)",
    scene=dict(
        xaxis_title='X (cm)',
        yaxis_title='Y (cm)',
        zaxis_title='Z (cm)'
    )
)

fig.show()

FileNotFoundError: [Errno 2] No such file or directory: 'grouting_final.csv.xlsx - 表格数据 (2).csv'

In [2]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import os
import io

# ================= 1. 智能文件加载模块 =================
def load_data_smart():
    # 关键词匹配：寻找文件名包含 'grouting' 且是 .csv 的文件
    files = [f for f in os.listdir('.') if 'grouting' in f and '.csv' in f]

    df = None
    filename = ""

    if len(files) > 0:
        # 如果找到了文件，取第一个
        filename = files[0]
        print(f"✅ 自动找到文件: {filename}")
        try:
            df = pd.read_csv(filename)
        except:
            print("⚠️ CSV读取失败，尝试作为Excel读取...")
            try:
                df = pd.read_excel(filename)
            except:
                pass

    # 如果没找到文件，或者读取失败，且我们在 Colab 环境，则提示上传
    if df is None:
        try:
            from google.colab import files as colab_files
            print("❌ 未找到文件。请点击下方按钮上传您的 CSV 文件：")
            uploaded = colab_files.upload()
            filename = list(uploaded.keys())[0]
            print(f"✅ 文件上传成功: {filename}")
            # 读取上传的文件
            try:
                df = pd.read_csv(io.BytesIO(uploaded[filename]))
            except:
                df = pd.read_excel(io.BytesIO(uploaded[filename]))
        except ImportError:
            print("❌ 错误：未找到文件，且不在 Colab 环境无法自动上传。请检查路径。")
            return None, None

    return df, filename

# ================= 2. 核心计算模块 =================
def calculate_3d_velocity(df):
    print("⏳ 正在计算 3D 速率...")

    # 1. 清洗列名 (防止有空格)
    df.columns = [c.strip() for c in df.columns]

    # 2. 自动识别列 (兼容不同命名)
    # 寻找包含 Time, X, Y, Z 的列
    t_col = next((c for c in df.columns if 'time' in c.lower() or 'arrival' in c.lower()), None)
    x_col = next((c for c in df.columns if 'x' in c.lower()), None)
    y_col = next((c for c in df.columns if 'y' in c.lower()), None)
    z_col = next((c for c in df.columns if 'z' in c.lower()), None)

    if not all([t_col, x_col, y_col, z_col]):
        print(f"⚠️ 列名识别失败。检测到的列: {df.columns}")
        return None

    # 3. 时间处理
    # 转换为 datetime 对象
    df['Time_Obj'] = pd.to_datetime(df[t_col], format='%H:%M:%S', errors='coerce')
    # 如果转换失败（可能是数字格式），尝试直接读取
    if df['Time_Obj'].isnull().all():
         df['Time_Sec'] = df[t_col] # 假设已经是秒
    else:
        min_time = df['Time_Obj'].min()
        df['Time_Sec'] = (df['Time_Obj'] - min_time).dt.total_seconds()

    # 按时间排序
    df = df.sort_values('Time_Sec').reset_index(drop=True)

    # 4. 速率计算 (最近邻算法)
    velocities = []
    coords = df[[x_col, y_col, z_col]].values
    times = df['Time_Sec'].values

    for i in range(len(df)):
        current_pos = coords[i]
        current_time = times[i]

        # 筛选出“过去”的点 (时间 < 当前时间)
        earlier_mask = times < current_time

        if not np.any(earlier_mask):
            velocities.append(0) # 第一个点速率设为0
            continue

        earlier_coords = coords[earlier_mask]
        earlier_times = times[earlier_mask]

        # 计算距离
        dists = np.linalg.norm(earlier_coords - current_pos, axis=1)

        # 找到最近的前驱点
        min_dist_idx = np.argmin(dists)
        min_dist = dists[min_dist_idx]

        # 计算时间差
        time_diff = current_time - earlier_times[min_dist_idx]

        # 计算速率 v = d / t
        if time_diff > 0.001: # 避免除以0
            v = min_dist / time_diff
        else:
            v = 0
        velocities.append(v)

    df['Calculated_Velocity'] = velocities

    # 移除异常值（比如第一帧可能导致极高速度，或者噪点）
    # 这里简单处理：限制最大显示速度为 95% 分位数，避免红色太少
    max_v = df['Calculated_Velocity'].quantile(0.98)
    if max_v > 0:
        print(f"ℹ️ 速率统计: 平均 {df['Calculated_Velocity'].mean():.2f} cm/s, 最大(截断前) {df['Calculated_Velocity'].max():.2f} cm/s")

    return df, x_col, y_col, z_col, t_col

# ================= 3. 运行主程序 =================

# A. 加载数据
df_raw, filename = load_data_smart()

if df_raw is not None:
    # B. 计算
    result_df, x_c, y_c, z_c, t_c = calculate_3d_velocity(df_raw)

    if result_df is not None:
        # C. 绘图
        print("📊 正在生成 3D 图表...")

        fig = go.Figure(data=[go.Scatter3d(
            x=result_df[x_c],
            y=result_df[y_c],
            z=result_df[z_c],
            mode='markers',
            marker=dict(
                size=6,
                color=result_df['Calculated_Velocity'], # 颜色映射速率
                colorscale='Jet',                       # 蓝->红 渐变
                cmin=0,
                cmax=result_df['Calculated_Velocity'].quantile(0.95), # 让颜色分布更均匀
                colorbar=dict(title="扩散速率 (cm/s)"),
                opacity=0.8
            ),
            # 鼠标悬停显示的文字
            text=[f"时间: {t}<br>速率: {v:.2f} cm/s<br>位置: ({x},{y},{z})"
                  for t, v, x, y, z in zip(result_df[t_c], result_df['Calculated_Velocity'],
                                           result_df[x_c], result_df[y_c], result_df[z_c])],
            hoverinfo='text'
        )])

        fig.update_layout(
            title=f"3D 注浆扩散速率场 - {filename}",
            width=900,
            height=700,
            scene=dict(
                xaxis_title='X (cm)',
                yaxis_title='Y (cm)',
                zaxis_title='Z (cm)',
                aspectmode='data' # 保持真实 xyz 比例
            ),
            margin=dict(l=0, r=0, b=0, t=40)
        )

        fig.show()
        print("✅ 完成！您可以旋转缩放上方的 3D 图。")

❌ 未找到文件。请点击下方按钮上传您的 CSV 文件：


Saving grouting_final.csv.xlsx to grouting_final.csv.xlsx
✅ 文件上传成功: grouting_final.csv.xlsx
⏳ 正在计算 3D 速率...
ℹ️ 速率统计: 平均 0.18 cm/s, 最大(截断前) 4.02 cm/s
📊 正在生成 3D 图表...


✅ 完成！您可以旋转缩放上方的 3D 图。


In [1]:
# ==========================================
# 第一步：环境配置与文件上传
# ==========================================
import os
import sys

# 1. 自动安装必要的库
print("正在安装绘图库 pyecharts...")
!pip install pyecharts pandas openpyxl -q

# 2. 导入库
import pandas as pd
import numpy as np
from google.colab import files
from pyecharts import options as opts
from pyecharts.charts import Scatter3D, Timeline

# 3. 上传文件 (运行后会出现上传按钮)
print("\n👇 请点击下方的【选择文件】按钮，上传您的 grouting_final.csv.xlsx 文件")
uploaded = files.upload()

# 获取上传的文件名
if not uploaded:
    print("❌ 未上传任何文件，程序终止。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 已获取文件: {file_name}")

    # ==========================================
    # 第二步：数据读取与处理
    # ==========================================
    try:
        # 智能读取 (Excel 或 CSV)
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try:
                df = pd.read_excel(file_name)
            except:
                df = pd.read_csv(file_name)

        # 清洗列名
        df.columns = [c.strip() for c in df.columns]

        # 检查关键列
        required_cols = ['X_cm', 'Y_cm', 'Z_cm', 'Arrival_Time_s']
        if not all(col in df.columns for col in required_cols):
            raise ValueError(f"数据缺少必要列，请确保包含: {required_cols}")

        # 时间转换
        df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

        # 确定源点 (最早时刻)
        min_idx = df['Time_Obj'].idxmin()
        source_row = df.loc[min_idx]
        s_time = source_row['Time_Obj']
        sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

        # 计算速度逻辑
        def calc_speed(row):
            if pd.isna(row['Time_Obj']): return 0
            if row.name == min_idx: return -1
            dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
            diff = (row['Time_Obj'] - s_time).total_seconds()
            return dist / diff if diff > 0 else 0

        df['Speed'] = df.apply(calc_speed, axis=1)
        # 修正源点速度为最大值
        max_sp = df[df['Speed'] != -1]['Speed'].max()
        df.loc[df['Speed'] == -1, 'Speed'] = max_sp

        # 生成时间列表 (取数据中存在的时刻)
        time_list = sorted(list(set(df['Arrival_Time_s'].dropna().astype(str))))
        # 或者指定固定时间段
        # time_list = ["10:01:00", "10:02:00", "10:03:00", "10:04:00", "10:05:00", "10:06:00", "10:07:00", "10:08:00", "10:09:00", "10:10:00", "10:11:00", "10:12:00"]

        print(f"数据处理完毕，共 {len(time_list)} 个时间点。正在生成 3D 图表...")

        # ==========================================
        # 第三步：生成图表 (兼容模式)
        # ==========================================
        timeline = Timeline(init_opts=opts.InitOpts(width="100%", height="100vh", bg_color="#ffffff"))
        timeline.add_schema(play_interval=1500, is_auto_play=True)

        for t_str in time_list:
            curr = pd.to_datetime(t_str, format='%H:%M:%S')
            mask = df['Time_Obj'] <= curr
            data = df[mask][['X_cm','Y_cm','Z_cm','Speed']].values.tolist()
            # 强制转换为原生 float
            data = [[float(x), float(y), float(z), float(v)] for x,y,z,v in data]

            scatter = (
                Scatter3D()
                .add(
                    series_name="浆液扩散",
                    data=data,
                    xaxis3d_opts=opts.Axis3DOpts(name="X", type_="value"),
                    yaxis3d_opts=opts.Axis3DOpts(name="Y", type_="value"),
                    zaxis3d_opts=opts.Axis3DOpts(name="Z", type_="value"),
                    # 使用字典配置绕过 grid3D 报错
                    grid3d_opts={
                        "boxWidth": 100,
                        "boxDepth": 100,
                        "boxHeight": 40,
                        "viewControl": {
                            "autoRotate": False,     # 禁止旋转
                            "rotateSensitivity": 1,  # 允许拖拽
                            "alpha": 30, "beta": 30  # 默认视角
                        },
                        "environment": "#ffffff"
                    }
                )
                .set_global_opts(
                    title_opts=opts.TitleOpts(
                        title=f"时刻: {t_str}", pos_left="center",
                        title_textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    # 使用字典配置绕过 visualMap 报错
                    visualmap_opts={
                        "type": "continuous",
                        "min": 0, "max": float(max_sp),
                        "dimension": 3,
                        "inRange": {"color": ['#313695', '#4575b4', '#74add1', '#ffffbf', '#f46d43', '#d73027']},
                        "right": "30", "top": "center",
                        "text": ["高速", "低速"],
                        "calculable": True,
                        "textStyle": {"color": "#333"}
                    },
                    tooltip_opts=opts.TooltipOpts(formatter="时刻: "+t_str+"<br/>坐标: (@c0, @c1, @c2)<br/>速度: @c3")
                )
            )
            timeline.add(scatter, time_point=t_str)

        # ==========================================
        # 第四步：保存与下载
        # ==========================================
        output_file = "grouting_3d_colab.html"
        timeline.render(output_file)

        print(f"🎉 成功生成！正在自动下载 {output_file} ...")
        files.download(output_file)

    except Exception as e:
        print(f"❌ 运行出错: {e}")

正在安装绘图库 pyecharts...
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 153.9/153.9 kB 5.4 MB/s eta 0:00:00

👇 请点击下方的【选择文件】按钮，上传您的 grouting_final.csv.xlsx 文件


Saving grouting_final.csv.xlsx to grouting_final.csv.xlsx
✅ 已获取文件: grouting_final.csv.xlsx
数据处理完毕，共 36 个时间点。正在生成 3D 图表...
🎉 成功生成！正在自动下载 grouting_3d_colab.html ...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [2]:
# ==========================================
# 0. 环境安装与配置
# ==========================================
print("正在安装必要的计算与绘图库...")
!pip install pyecharts pandas scipy -q

import pandas as pd
import numpy as np
import os
from scipy.interpolate import griddata  # 核心插值库
from google.colab import files
from pyecharts import options as opts
from pyecharts.charts import Scatter3D, Timeline
from pyecharts.globals import ThemeType
from IPython.display import display, HTML

# ==========================================
# 1. 上传数据文件
# ==========================================
print("\n👇 请点击下方按钮上传 Excel/CSV 文件 (例如 grouting_final.csv.xlsx)")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，程序结束。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件已接收: {file_name}")

    # ==========================================
    # 2. 数据读取与基础计算 (与之前相同)
    # ==========================================
    try:
        # 智能读取
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)

        df.columns = [c.strip() for c in df.columns]
        df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

        # 确定源点
        min_idx = df['Time_Obj'].idxmin()
        source_row = df.loc[min_idx]
        s_time = source_row['Time_Obj']
        sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

        # 计算原始点速度
        def calc_speed(row):
            if pd.isna(row['Time_Obj']): return 0
            if row.name == min_idx: return -1
            d = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
            t = (row['Time_Obj'] - s_time).total_seconds()
            return d/t if t>0 else 0

        df['Speed'] = df.apply(calc_speed, axis=1)
        max_sp = df[df['Speed'] != -1]['Speed'].max()
        df.loc[df['Speed'] == -1, 'Speed'] = max_sp # 修正源点

        print(f"基础数据计算完成。最大速度: {max_sp:.2f} cm/s")

        # ==========================================
        # 3. 核心功能：3D 空间插值 (Interpolation)
        # ==========================================
        # 生成一个密集的网格，用于模拟连续场
        # X: 0-100, Y: 0-100, Z: 0-20 (根据您的数据范围调整)
        # step=5 表示每隔 5cm 生成一个插值点
        grid_x, grid_y, grid_z = np.mgrid[0:105:5, 0:105:5, 0:25:5]

        def get_interpolated_data(current_time_str):
            """
            输入时刻，返回经过空间插值后的密集点云数据
            """
            curr = pd.to_datetime(current_time_str, format='%H:%M:%S')

            # 1. 获取当前时刻已有的真实点
            mask = df['Time_Obj'] <= curr
            real_points = df[mask]

            if len(real_points) < 4: # 点太少无法插值
                return []

            # 提取坐标(points) 和 值(values)
            points = real_points[['X_cm', 'Y_cm', 'Z_cm']].values
            values = real_points['Speed'].values

            # 2. 使用 scipy 进行 3D 插值 (linear 线性插值, nearest 最近邻插值)
            # method='nearest' 能保证填充整个空间，'linear' 更平滑但只在凸包内有效
            # 这里我们用 'nearest' 来模拟浆液扩散的整体场
            grid_v = griddata(points, values, (grid_x, grid_y, grid_z), method='nearest')

            # 3. 将网格转回点列表 [x, y, z, v]
            flat_data = []
            it = np.nditer(grid_v, flags=['multi_index'])
            while not it.finished:
                val = it[0]
                if not np.isnan(val):
                    idx = it.multi_index
                    # 只有当速度大于0才显示
                    if val > 0:
                        x = int(grid_x[idx])
                        y = int(grid_y[idx])
                        z = int(grid_z[idx])
                        flat_data.append([x, y, z, round(float(val), 2)])
                it.iternext()

            return flat_data

        # ==========================================
        # 4. 生成 3D 梯度可视化
        # ==========================================
        print("正在进行空间插值运算（这可能需要几秒钟）...")

        timeline = Timeline(init_opts=opts.InitOpts(width="100%", height="800px", bg_color="#ffffff"))
        timeline.add_schema(play_interval=1000, is_auto_play=True)

        # 选取关键时间点进行展示
        time_list = sorted(list(set(df['Arrival_Time_s'].dropna().astype(str))))
        # 仅取最后几个时刻展示完整效果，或者全部展示
        # time_list = time_list[-5:]

        for t_str in time_list:
            # 获取插值后的密集数据
            dense_data = get_interpolated_data(t_str)

            if not dense_data: continue

            scatter = (
                Scatter3D()
                .add(
                    series_name="速度场",
                    data=dense_data,
                    xaxis3d_opts=opts.Axis3DOpts(name="X", type_="value"),
                    yaxis3d_opts=opts.Axis3DOpts(name="Y", type_="value"),
                    zaxis3d_opts=opts.Axis3DOpts(name="Z", type_="value"),
                    grid3d_opts={
                        "boxWidth": 100, "boxDepth": 100, "boxHeight": 40,
                        "viewControl": {"autoRotate": False, "alpha": 30, "beta": 30},
                        "environment": "#ffffff"
                    }
                )
                .set_global_opts(
                    title_opts=opts.TitleOpts(
                        title=f"时刻 {t_str} - 速度梯度场", pos_left="center",
                        title_textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    visualmap_opts=opts.VisualMapOpts(
                        max_=float(max_sp), min_=0,
                        dimension=3,
                        # 使用彩虹色谱模拟热力图效果
                        range_color=['#0d47a1', '#2196f3', '#4dd0e1', '#fff176', '#ff9800', '#d50000'],
                        pos_right="10", pos_top="center", title="速度 (cm/s)",
                        textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    tooltip_opts=opts.TooltipOpts(
                        formatter=lambda params: f"位置: ({params.value[0]}, {params.value[1]}, {params.value[2]})<br/>推算速度: {params.value[3]} cm/s"
                    )
                )
            )
            timeline.add(scatter, time_point=t_str)

        # ==========================================
        # 5. 输出结果
        # ==========================================
        out_file = "grouting_gradient_field.html"
        timeline.render(out_file)

        print(f"\n🎉 梯度场生成完毕！")
        print("1. 正在尝试在下方直接显示交互图...")
        try:
            # 在 Colab 中直接显示 HTML
            display(HTML(filename=out_file))
        except Exception as e:
            print(f"内嵌显示失败 ({e})，请下载文件查看。")

        print(f"2. 正在下载文件: {out_file}")
        files.download(out_file)

    except Exception as e:
        import traceback
        print(f"❌ 运行错误: {e}")
        print(traceback.format_exc())

正在安装必要的计算与绘图库...

👇 请点击下方按钮上传 Excel/CSV 文件 (例如 grouting_final.csv.xlsx)


Saving grouting_final.csv.xlsx to grouting_final.csv (1).xlsx
✅ 文件已接收: grouting_final.csv (1).xlsx
基础数据计算完成。最大速度: 4.00 cm/s
正在进行空间插值运算（这可能需要几秒钟）...
❌ 运行错误: VisualMapOpts.__init__() got an unexpected keyword argument 'title'
Traceback (most recent call last):
  File "/tmp/ipython-input-3885743927.py", line 148, in <cell line: 0>
    visualmap_opts=opts.VisualMapOpts(
                   ^^^^^^^^^^^^^^^^^^^
TypeError: VisualMapOpts.__init__() got an unexpected keyword argument 'title'



In [3]:
# ==========================================
# 0. 环境安装
# ==========================================
# 这一步会自动安装需要的库，无需手动操作
print("正在初始化环境，安装绘图库...")
!pip install pyecharts pandas scipy openpyxl -q

import pandas as pd
import numpy as np
import os
from scipy.interpolate import griddata
from google.colab import files
from pyecharts import options as opts
from pyecharts.charts import Scatter3D, Timeline
from IPython.display import display, HTML

# ==========================================
# 1. 上传文件
# ==========================================
print("\n👇 请点击下方的【选择文件】按钮，上传您的 Excel/CSV 数据文件")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，请重新运行。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件已接收: {file_name}")

    # ==========================================
    # 2. 数据读取与基础计算
    # ==========================================
    try:
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)

        df.columns = [c.strip() for c in df.columns]
        df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

        # 确定源点
        min_idx = df['Time_Obj'].idxmin()
        source_row = df.loc[min_idx]
        s_time = source_row['Time_Obj']
        sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

        # 计算原始点速度
        def calc_speed(row):
            if pd.isna(row['Time_Obj']): return 0
            if row.name == min_idx: return -1
            d = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
            t = (row['Time_Obj'] - s_time).total_seconds()
            return d/t if t>0 else 0

        df['Speed'] = df.apply(calc_speed, axis=1)
        max_sp = df[df['Speed'] != -1]['Speed'].max()
        df.loc[df['Speed'] == -1, 'Speed'] = max_sp

        print(f"基础数据计算完成。最大速度: {max_sp:.2f} cm/s")

        # ==========================================
        # 3. 核心：3D 空间插值 (梯度计算)
        # ==========================================
        # 创建密集网格：范围根据您的数据大致设定 (0-100cm)
        # step=4 表示每 4cm 取一个点，数值越小图越细腻，但计算越慢
        grid_x, grid_y, grid_z = np.mgrid[0:105:4, 0:105:4, 0:25:4]

        def get_interpolated_data(current_time_str):
            curr = pd.to_datetime(current_time_str, format='%H:%M:%S')
            mask = df['Time_Obj'] <= curr
            real_points = df[mask]

            if len(real_points) < 4: return [] # 点太少无法插值

            # 提取真实点坐标和值
            points = real_points[['X_cm', 'Y_cm', 'Z_cm']].values
            values = real_points['Speed'].values

            # 使用 'nearest' 算法填充整个空间，模拟连续介质
            grid_v = griddata(points, values, (grid_x, grid_y, grid_z), method='nearest')

            # 转换为 ECharts 需要的 [x, y, z, value] 格式
            flat_data = []
            it = np.nditer(grid_v, flags=['multi_index'])
            while not it.finished:
                val = it[0]
                if not np.isnan(val) and val > 0: # 只显示有效速度
                    idx = it.multi_index
                    flat_data.append([
                        int(grid_x[idx]),
                        int(grid_y[idx]),
                        int(grid_z[idx]),
                        round(float(val), 2)
                    ])
                it.iternext()
            return flat_data

        # ==========================================
        # 4. 生成可视化 (修复 VisualMap 报错)
        # ==========================================
        print("正在进行空间插值并生成图表（请稍候）...")

        timeline = Timeline(init_opts=opts.InitOpts(width="100%", height="800px", bg_color="#ffffff"))
        timeline.add_schema(play_interval=2000, is_auto_play=True)

        time_list = sorted(list(set(df['Arrival_Time_s'].dropna().astype(str))))

        for t_str in time_list:
            dense_data = get_interpolated_data(t_str)
            if not dense_data: continue

            scatter = (
                Scatter3D()
                .add(
                    series_name="速度梯度",
                    data=dense_data,
                    xaxis3d_opts=opts.Axis3DOpts(name="X", type_="value"),
                    yaxis3d_opts=opts.Axis3DOpts(name="Y", type_="value"),
                    zaxis3d_opts=opts.Axis3DOpts(name="Z", type_="value"),
                    # 字典配置 grid3D，防止报错
                    grid3d_opts={
                        "boxWidth": 100, "boxDepth": 100, "boxHeight": 40,
                        "viewControl": {"autoRotate": False, "alpha": 30, "beta": 30},
                        "environment": "#ffffff"
                    }
                )
                .set_global_opts(
                    title_opts=opts.TitleOpts(
                        title=f"时刻 {t_str} - 速度场", pos_left="center",
                        title_textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    # 【关键修复】移除了报错的 title 参数，改用 range_text
                    visualmap_opts=opts.VisualMapOpts(
                        max_=float(max_sp),
                        min_=0,
                        dimension=3,
                        range_color=['#0d47a1', '#2196f3', '#4dd0e1', '#fff176', '#ff9800', '#d50000'],
                        pos_right="10",
                        pos_top="center",
                        range_text=['高速', '低速'], # 这里替代了 title
                        textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    tooltip_opts=opts.TooltipOpts(
                        formatter=lambda p: f"位置:({p.value[0]},{p.value[1]},{p.value[2]})<br>速度:{p.value[3]}"
                    )
                )
            )
            timeline.add(scatter, time_point=t_str)

        out_file = "grouting_gradient_result.html"
        timeline.render(out_file)

        print(f"\n🎉 处理完成！文件已生成: {out_file}")
        print("正在尝试自动下载...")
        files.download(out_file)

    except Exception as e:
        import traceback
        print(f"❌ 运行依然报错: {e}")
        print(traceback.format_exc())

正在初始化环境，安装绘图库...

👇 请点击下方的【选择文件】按钮，上传您的 Excel/CSV 数据文件


Saving grouting_final.csv.xlsx to grouting_final.csv (2).xlsx
✅ 文件已接收: grouting_final.csv (2).xlsx
基础数据计算完成。最大速度: 4.00 cm/s
正在进行空间插值并生成图表（请稍候）...

🎉 处理完成！文件已生成: grouting_gradient_result.html
正在尝试自动下载...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [4]:
# ==========================================
# 0. 环境初始化
# ==========================================
print("正在安装计算与绘图库...")
!pip install pyecharts pandas scipy openpyxl -q

import pandas as pd
import numpy as np
import os
from scipy.interpolate import griddata
from google.colab import files
from pyecharts import options as opts
from pyecharts.charts import Scatter3D, Timeline
from IPython.display import display, HTML

# ==========================================
# 1. 上传数据文件
# ==========================================
print("\n👇 请点击下方的【选择文件】按钮，上传数据文件 (例如 grouting_final.csv.xlsx)")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，请重新运行。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件已接收: {file_name}")

    # ==========================================
    # 2. 速度计算模块 (Speed Calculation)
    # ==========================================
    # 读取文件
    try:
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)

        # 清洗数据
        df.columns = [c.strip() for c in df.columns]
        df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

        # 自动识别注浆源（最早到达的点）
        min_idx = df['Time_Obj'].idxmin()
        source_row = df.loc[min_idx]
        s_time = source_row['Time_Obj']
        sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

        print(f"📍 注浆源点坐标: ({sx}, {sy}, {sz})  起始时间: {s_time.time()}")

        # 定义速度计算函数：v = 距离 / 时间差
        def calc_speed(row):
            if pd.isna(row['Time_Obj']): return 0
            if row.name == min_idx: return -1 # 标记源点

            # 计算欧氏距离
            dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
            # 计算时间差 (秒)
            t_diff = (row['Time_Obj'] - s_time).total_seconds()

            # 计算速度 (cm/s)
            return dist / t_diff if t_diff > 0 else 0

        # 应用计算
        df['Speed'] = df.apply(calc_speed, axis=1)

        # 将源点速度设为除去源点外的最大速度（模拟喷射口高速）
        max_sp = df[df['Speed'] != -1]['Speed'].max()
        df.loc[df['Speed'] == -1, 'Speed'] = max_sp

        print("\n📊 各点速度计算结果预览 (前5行):")
        print(df[['Sensor_ID', 'X_cm', 'Y_cm', 'Z_cm', 'Arrival_Time_s', 'Speed']].head())

        # ==========================================
        # 3. 梯度插值与切片提取 (Interpolation & Slicing)
        # ==========================================
        # 定义您指定的切片时刻列表
        target_slices = [
            "10:01:00", "10:02:00", "10:03:00", "10:04:00",
            "10:05:00", "10:06:00", "10:07:00", "10:08:00",
            "10:09:00", "10:10:00", "10:11:00", "10:12:00"
        ]

        # 创建空间网格 (Resolution: 5cm)
        # 越小越精细，但计算越慢。建议 4-5cm。
        grid_x, grid_y, grid_z = np.mgrid[0:105:5, 0:105:5, 0:25:5]

        def get_gradient_slice(slice_time_str):
            """计算特定时刻的 3D 速度梯度切片"""
            curr_time = pd.to_datetime(slice_time_str, format='%H:%M:%S')

            # 筛选当前时刻已波及的区域
            mask = df['Time_Obj'] <= curr_time
            valid_points = df[mask]

            # 如果点太少(少于4个)，无法构建3D几何体，返回空
            if len(valid_points) < 4:
                return []

            # 提取真实点数据
            points = valid_points[['X_cm', 'Y_cm', 'Z_cm']].values
            values = valid_points['Speed'].values

            # ★ 核心算法：3D 空间插值 (Nearest Neighbor)
            # 将稀疏的传感器点扩展为连续的实体场
            grid_v = griddata(points, values, (grid_x, grid_y, grid_z), method='nearest')

            # 格式化输出
            flat_data = []
            it = np.nditer(grid_v, flags=['multi_index'])
            while not it.finished:
                val = it[0]
                # 过滤无效值和零值，只保留有浆液的区域
                if not np.isnan(val) and val > 0:
                    idx = it.multi_index
                    flat_data.append([
                        int(grid_x[idx]),
                        int(grid_y[idx]),
                        int(grid_z[idx]),
                        round(float(val), 2)
                    ])
                it.iternext()
            return flat_data

        # ==========================================
        # 4. 生成 3D 可视化
        # ==========================================
        print(f"\n⚙️ 正在提取 {len(target_slices)} 个时间切片并进行梯度计算...")

        timeline = Timeline(init_opts=opts.InitOpts(width="100%", height="800px", bg_color="#ffffff"))
        timeline.add_schema(play_interval=1500, is_auto_play=True)

        for t_str in target_slices:
            # 获取该时刻的梯度数据
            slice_data = get_gradient_slice(t_str)

            if not slice_data:
                print(f"  - {t_str}: 数据不足，跳过绘制")
                # 也可以添加一个空图防止时间轴断裂，这里选择跳过以展示有效数据
                # 为保证时间轴连续，我们可以加一个空点
                slice_data = [[0,0,0,0]]

            scatter = (
                Scatter3D()
                .add(
                    series_name="速度梯度场",
                    data=slice_data,
                    xaxis3d_opts=opts.Axis3DOpts(name="X (cm)", type_="value"),
                    yaxis3d_opts=opts.Axis3DOpts(name="Y (cm)", type_="value"),
                    zaxis3d_opts=opts.Axis3DOpts(name="Z (cm)", type_="value"),
                    grid3d_opts={
                        "boxWidth": 100, "boxDepth": 100, "boxHeight": 40,
                        "viewControl": {"autoRotate": False, "alpha": 30, "beta": 30},
                        "environment": "#ffffff"
                    }
                )
                .set_global_opts(
                    title_opts=opts.TitleOpts(
                        title=f"时刻 {t_str} - 速度切片",
                        pos_left="center",
                        title_textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    visualmap_opts=opts.VisualMapOpts(
                        max_=float(max_sp), min_=0,
                        dimension=3,
                        # 使用热力图色谱 (蓝->青->黄->红)
                        range_color=['#0d47a1', '#2196f3', '#4dd0e1', '#fff176', '#ff9800', '#d50000'],
                        pos_right="10", pos_top="center",
                        range_text=['高速', '低速'], # 替代 title，兼容性更好
                        textstyle_opts=opts.TextStyleOpts(color="#333")
                    ),
                    tooltip_opts=opts.TooltipOpts(
                        formatter=lambda p: f"位置:({p.value[0]},{p.value[1]},{p.value[2]})<br>速度:{p.value[3]} cm/s"
                    )
                )
            )
            timeline.add(scatter, time_point=t_str)

        # 保存结果
        output_file = "grouting_speed_slices.html"
        timeline.render(output_file)

        print(f"\n🎉 计算与渲染完成！")
        print(f"正在下载结果文件: {output_file}")
        files.download(output_file)

    except Exception as e:
        import traceback
        print(f"❌ 运行出错: {e}")
        print(traceback.format_exc())

正在安装计算与绘图库...

👇 请点击下方的【选择文件】按钮，上传数据文件 (例如 grouting_final.csv.xlsx)


Saving grouting_final.csv.xlsx to grouting_final.csv (3).xlsx
✅ 文件已接收: grouting_final.csv (3).xlsx
📍 注浆源点坐标: (100, 50, 20)  起始时间: 10:02:05

📊 各点速度计算结果预览 (前5行):
   Sensor_ID  X_cm  Y_cm  Z_cm Arrival_Time_s     Speed
0          1     0     0     0       10:09:05  0.270424
1          2    25     0     0       10:08:05  0.256475
2          3    50     0     0       10:06:15  0.293939
3          4    75     0     0       10:04:05  0.494764
4          5   100     0     0       10:03:35  0.598352

⚙️ 正在提取 12 个时间切片并进行梯度计算...
  - 10:01:00: 数据不足，跳过绘制
  - 10:02:00: 数据不足，跳过绘制

🎉 计算与渲染完成！
正在下载结果文件: grouting_speed_slices.html


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [5]:
# ==========================================
# 1. 环境初始化 (自动安装)
# ==========================================
print("正在初始化环境，安装绘图库...")
!pip install pyecharts pandas scipy openpyxl -q

import pandas as pd
import numpy as np
import os
from scipy.interpolate import griddata
from google.colab import files
from pyecharts import options as opts
from pyecharts.charts import Scatter3D, Timeline
from pyecharts.globals import CurrentConfig, NotebookType
from IPython.display import display, HTML

# 配置 PyEcharts 以便在 Colab 中显示
CurrentConfig.NOTEBOOK_TYPE = NotebookType.JUPYTER_LAB

# ==========================================
# 2. 上传数据
# ==========================================
print("\n👇 请点击下方按钮上传您的数据文件 (例如 grouting_final.csv.xlsx)")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，请重新运行。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件已接收: {file_name}")

    # ==========================================
    # 3. 数据处理与速度计算
    # ==========================================
    # 读取数据
    try:
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)
    except Exception as e:
        print(f"❌ 读取失败: {e}")
        raise

    # 数据清洗
    df.columns = [c.strip() for c in df.columns]
    df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

    # 确定注浆源（最早到达点）
    min_idx = df['Time_Obj'].idxmin()
    source_row = df.loc[min_idx]
    s_time = source_row['Time_Obj']
    sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

    print(f"📍 注浆源点: ({sx}, {sy}, {sz})")

    # 计算速度 (v = dist / time)
    def calc_speed(row):
        if pd.isna(row['Time_Obj']): return 0
        if row.name == min_idx: return -1
        dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
        diff = (row['Time_Obj'] - s_time).total_seconds()
        return dist / diff if diff > 0 else 0

    df['Speed'] = df.apply(calc_speed, axis=1)
    max_sp = df[df['Speed'] != -1]['Speed'].max()
    df.loc[df['Speed'] == -1, 'Speed'] = max_sp # 修正源点速度

    print(f"⚡ 最大速度: {max_sp:.2f} cm/s")

    # ==========================================
    # 4. 梯度插值算法 (生成切片)
    # ==========================================
    # 定义目标时刻
    target_times = [
        "10:01:00", "10:02:00", "10:03:00", "10:04:00",
        "10:05:00", "10:06:00", "10:07:00", "10:08:00",
        "10:09:00", "10:10:00", "10:11:00", "10:12:00"
    ]

    # 创建插值网格 (步长 5cm，步长越小越精细但越慢)
    grid_x, grid_y, grid_z = np.mgrid[0:105:5, 0:105:5, 0:25:5]

    def get_interpolated_slice(time_str):
        """计算指定时刻的 3D 速度场切片"""
        curr = pd.to_datetime(time_str, format='%H:%M:%S')
        # 筛选该时刻已覆盖的区域
        mask = df['Time_Obj'] <= curr
        valid_df = df[mask]

        if len(valid_df) < 4: return [] # 点太少无法构建立体场

        points = valid_df[['X_cm', 'Y_cm', 'Z_cm']].values
        values = valid_df['Speed'].values

        # 空间插值 (Nearest)
        grid_v = griddata(points, values, (grid_x, grid_y, grid_z), method='nearest')

        # 格式化数据
        flat_data = []
        it = np.nditer(grid_v, flags=['multi_index'])
        while not it.finished:
            val = it[0]
            if not np.isnan(val) and val > 0:
                idx = it.multi_index
                flat_data.append([
                    int(grid_x[idx]), int(grid_y[idx]), int(grid_z[idx]),
                    round(float(val), 2)
                ])
            it.iternext()
        return flat_data

    # ==========================================
    # 5. 生成可视化 (直接显示)
    # ==========================================
    print("\n⚙️ 正在计算梯度场并生成图表 (请稍候)...")

    timeline = Timeline(init_opts=opts.InitOpts(width="100%", height="700px", bg_color="#ffffff"))
    timeline.add_schema(play_interval=1000, is_auto_play=True)

    for t_str in target_times:
        data = get_interpolated_slice(t_str)
        if not data: continue # 跳过无数据时刻

        scatter = (
            Scatter3D()
            .add(
                series_name="",
                data=data,
                xaxis3d_opts=opts.Axis3DOpts(name="X", type_="value"),
                yaxis3d_opts=opts.Axis3DOpts(name="Y", type_="value"),
                zaxis3d_opts=opts.Axis3DOpts(name="Z", type_="value"),
                # 使用字典配置，确保兼容性
                grid3d_opts={
                    "boxWidth": 100, "boxDepth": 100, "boxHeight": 40,
                    "viewControl": {"autoRotate": False, "alpha": 30, "beta": 30},
                    "environment": "#ffffff"
                }
            )
            .set_global_opts(
                title_opts=opts.TitleOpts(
                    title=f"时刻 {t_str}", pos_left="center",
                    title_textstyle_opts=opts.TextStyleOpts(color="#333")
                ),
                visualmap_opts=opts.VisualMapOpts(
                    max_=float(max_sp), min_=0,
                    dimension=3,
                    range_color=['#0d47a1', '#2196f3', '#4dd0e1', '#fff176', '#ff9800', '#d50000'],
                    pos_right="10", pos_top="center",
                    range_text=['高速', '低速'],
                    textstyle_opts=opts.TextStyleOpts(color="#333")
                ),
                tooltip_opts=opts.TooltipOpts(
                    formatter=lambda p: f"位置:({p.value[0]},{p.value[1]},{p.value[2]})<br>速度:{p.value[3]}"
                )
            )
        )
        timeline.add(scatter, time_point=t_str)

    # 在 Colab 中直接渲染 HTML
    print("🎉 计算完成！图表如下 (可拖动时间轴或鼠标旋转视图):")
    html_content = timeline.render_embed()
    display(HTML(html_content))

正在初始化环境，安装绘图库...

👇 请点击下方按钮上传您的数据文件 (例如 grouting_final.csv.xlsx)


Saving grouting_final.csv.xlsx to grouting_final.csv (4).xlsx
✅ 文件已接收: grouting_final.csv (4).xlsx
📍 注浆源点: (100, 50, 20)
⚡ 最大速度: 4.00 cm/s

⚙️ 正在计算梯度场并生成图表 (请稍候)...
🎉 计算完成！图表如下 (可拖动时间轴或鼠标旋转视图):


In [6]:
# ==========================================
# 0. 环境准备与配置
# ==========================================
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from google.colab import files
import os
import zipfile

# 配置绘图风格
plt.style.use('default')

# ==========================================
# 1. 上传数据文件
# ==========================================
print("👇 请点击下方按钮上传 Excel/CSV 数据文件 (例如 grouting_final.csv.xlsx)")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，请重新运行。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件接收成功: {file_name}")

    # ==========================================
    # 2. 数据读取与速度计算
    # ==========================================
    # 智能读取
    try:
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)
    except Exception as e:
        print(f"❌ 读取文件失败: {e}")
        raise

    # 数据清洗
    df.columns = [c.strip() for c in df.columns]
    df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

    # 确定源点 (最早到达的点)
    min_idx = df['Time_Obj'].idxmin()
    source_row = df.loc[min_idx]
    s_time = source_row['Time_Obj']
    sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

    print(f"📍 注浆源点: ({sx}, {sy}, {sz})，起始时间: {s_time.time()}")

    # 计算速度逻辑
    def calc_speed(row):
        if pd.isna(row['Time_Obj']): return 0
        if row.name == min_idx: return -1 # 标记源点
        dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
        diff = (row['Time_Obj'] - s_time).total_seconds()
        return dist / diff if diff > 0 else 0

    df['Speed'] = df.apply(calc_speed, axis=1)

    # 修正源点速度 (取非源点的最大值，避免绘图时颜色偏差)
    valid_speeds = df[df['Speed'] != -1]['Speed']
    max_sp = valid_speeds.max() if not valid_speeds.empty else 1.0
    df.loc[df['Speed'] == -1, 'Speed'] = max_sp

    # ==========================================
    # 3. 批量生成静态切片图
    # ==========================================
    target_times = [
        "10:01:00", "10:02:00", "10:03:00", "10:04:00",
        "10:05:00", "10:06:00", "10:07:00", "10:08:00",
        "10:09:00", "10:10:00", "10:11:00", "10:12:00"
    ]

    # 【关键】设置全局统一的坐标轴范围和颜色范围，确保图片之间可对比
    x_min, x_max = 0, 100  # 根据您的数据范围设定，也可使用 df['X_cm'].min()
    y_min, y_max = 0, 100
    z_min, z_max = 0, 40

    # 颜色映射范围 (0 到 最大速度)
    v_min, v_max = 0, max_sp

    generated_files = []
    print("\n⚙️ 开始生成 3D 切片图...")

    for t_str in target_times:
        curr = pd.to_datetime(t_str, format='%H:%M:%S')

        # 筛选：仅显示当前时刻及之前已到达的点 (累积显示)
        # 如果您只想要“当前这一秒新增加的点”，请联系我修改逻辑
        mask = df['Time_Obj'] <= curr
        subset = df[mask]

        # 即使没有数据，也生成一张空图，保持时间序列完整
        fig = plt.figure(figsize=(10, 8), dpi=100)
        ax = fig.add_subplot(111, projection='3d')

        if not subset.empty:
            # 绘制散点 (jet 颜色映射: 蓝=慢, 红=快)
            p = ax.scatter(
                subset['X_cm'], subset['Y_cm'], subset['Z_cm'],
                c=subset['Speed'], cmap='jet',
                vmin=v_min, vmax=v_max,
                s=100, edgecolors='k', alpha=0.9
            )
            # 添加颜色条
            cbar = fig.colorbar(p, ax=ax, shrink=0.6, pad=0.1)
            cbar.set_label('Speed (cm/s)', fontsize=10)

        # 设置标题和标签 (使用英文以防 Colab 中文乱码)
        ax.set_title(f"Time Slice: {t_str}", fontsize=15, fontweight='bold')
        ax.set_xlabel('X (cm)')
        ax.set_ylabel('Y (cm)')
        ax.set_zlabel('Z (cm)')

        # 锁定坐标轴范围
        ax.set_xlim(x_min, x_max)
        ax.set_ylim(y_min, y_max)
        ax.set_zlim(z_min, z_max)

        # 设置一个较好的观察视角
        ax.view_init(elev=30, azim=45)

        # 保存图片
        # 文件名处理：将 10:01:00 转为 100100，避免文件名非法字符
        safe_time_str = t_str.replace(':', '')
        filename = f"slice_{safe_time_str}.png"

        plt.savefig(filename, bbox_inches='tight')
        plt.close(fig) # 关闭画布释放内存

        generated_files.append(filename)
        print(f"  ✅ 已生成: {filename} (点数: {len(subset)})")

    # ==========================================
    # 4. 打包并下载
    # ==========================================
    zip_filename = "grouting_slices.zip"
    with zipfile.ZipFile(zip_filename, 'w') as zipf:
        for file in generated_files:
            zipf.write(file)

    print(f"\n🎉 全部处理完成！正在自动下载打包文件: {zip_filename}")
    files.download(zip_filename)

👇 请点击下方按钮上传 Excel/CSV 数据文件 (例如 grouting_final.csv.xlsx)


Saving grouting_final.csv.xlsx to grouting_final.csv (5).xlsx
✅ 文件接收成功: grouting_final.csv (5).xlsx
📍 注浆源点: (100, 50, 20)，起始时间: 10:02:05

⚙️ 开始生成 3D 切片图...
  ✅ 已生成: slice_100100.png (点数: 0)
  ✅ 已生成: slice_100200.png (点数: 0)
  ✅ 已生成: slice_100300.png (点数: 10)
  ✅ 已生成: slice_100400.png (点数: 18)
  ✅ 已生成: slice_100500.png (点数: 20)
  ✅ 已生成: slice_100600.png (点数: 22)
  ✅ 已生成: slice_100700.png (点数: 38)
  ✅ 已生成: slice_100800.png (点数: 49)
  ✅ 已生成: slice_100900.png (点数: 67)
  ✅ 已生成: slice_101000.png (点数: 73)
  ✅ 已生成: slice_101100.png (点数: 74)
  ✅ 已生成: slice_101200.png (点数: 74)

🎉 全部处理完成！正在自动下载打包文件: grouting_slices.zip


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [7]:
# ==========================================
# 0. 环境准备与配置
# ==========================================
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from google.colab import files
import os
import zipfile

# 配置绘图风格
plt.style.use('default')
# 设置字体以防中文乱码 (Colab默认环境可能不支持中文，这里用英文标签，数值标签是数字没问题)
plt.rcParams['axes.unicode_minus'] = False

# ==========================================
# 1. 上传数据文件
# ==========================================
print("👇 请点击下方按钮上传 Excel/CSV 数据文件 (例如 grouting_final.csv.xlsx)")
uploaded = files.upload()

if not uploaded:
    print("❌ 未上传文件，请重新运行。")
else:
    file_name = next(iter(uploaded))
    print(f"✅ 文件接收成功: {file_name}")

    # ==========================================
    # 2. 数据读取与速度计算
    # ==========================================
    # 智能读取
    try:
        if file_name.endswith('.csv'):
            df = pd.read_csv(file_name)
        else:
            try: df = pd.read_excel(file_name)
            except: df = pd.read_csv(file_name)
    except Exception as e:
        print(f"❌ 读取文件失败: {e}")
        raise

    # 数据清洗
    df.columns = [c.strip() for c in df.columns]
    df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

    # 确定源点 (最早到达的点)
    min_idx = df['Time_Obj'].idxmin()
    source_row = df.loc[min_idx]
    s_time = source_row['Time_Obj']
    sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

    print(f"📍 注浆源点: ({sx}, {sy}, {sz})，起始时间: {s_time.time()}")

    # 计算速度逻辑
    def calc_speed(row):
        if pd.isna(row['Time_Obj']): return 0
        if row.name == min_idx: return -1 # 标记源点
        dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
        diff = (row['Time_Obj'] - s_time).total_seconds()
        return dist / diff if diff > 0 else 0

    df['Speed'] = df.apply(calc_speed, axis=1)

    # 修正源点速度 (取非源点的最大值)
    valid_speeds = df[df['Speed'] != -1]['Speed']
    max_sp = valid_speeds.max() if not valid_speeds.empty else 1.0
    df.loc[df['Speed'] == -1, 'Speed'] = max_sp

    # ==========================================
    # 3. 批量生成带数值标签的切片图
    # ==========================================
    target_times = [
        "10:01:00", "10:02:00", "10:03:00", "10:04:00",
        "10:05:00", "10:06:00", "10:07:00", "10:08:00",
        "10:09:00", "10:10:00", "10:11:00", "10:12:00"
    ]

    # 设置全局统一的坐标轴范围和颜色范围
    x_min, x_max = 0, 100
    y_min, y_max = 0, 100
    z_min, z_max = 0, 40
    v_min, v_max = 0, max_sp

    generated_files = []
    print("\n⚙️ 开始生成带数值标签的 3D 切片图...")

    for t_str in target_times:
        curr = pd.to_datetime(t_str, format='%H:%M:%S')

        # 筛选数据
        mask = df['Time_Obj'] <= curr
        subset = df[mask]

        # 创建画布
        fig = plt.figure(figsize=(12, 10), dpi=100) # 稍微加大画布以便显示文字
        ax = fig.add_subplot(111, projection='3d')

        if not subset.empty:
            # 1. 绘制散点
            p = ax.scatter(
                subset['X_cm'], subset['Y_cm'], subset['Z_cm'],
                c=subset['Speed'], cmap='jet',
                vmin=v_min, vmax=v_max,
                s=80, edgecolors='k', alpha=0.9
            )

            # 2. 【核心新增】添加数值标签
            for _, row in subset.iterrows():
                # 获取坐标和速度
                x, y, z = row['X_cm'], row['Y_cm'], row['Z_cm']
                speed_val = row['Speed']

                # 在点旁边添加文本
                # '%.2f' % speed_val 表示保留两位小数
                label_text = f"{speed_val:.2f}"

                ax.text(
                    x, y, z + 1.5,   # z + 1.5 让文字稍微浮在点上方，不遮挡点
                    label_text,
                    fontsize=8,      # 字体大小
                    color='black',   # 文字颜色
                    ha='center',     # 水平居中
                    va='bottom'      # 垂直对齐底部
                )

            # 添加颜色条
            cbar = fig.colorbar(p, ax=ax, shrink=0.6, pad=0.1)
            cbar.set_label('Speed (cm/s)', fontsize=10)

        # 设置标题和标签
        ax.set_title(f"Time Slice: {t_str}", fontsize=15, fontweight='bold')
        ax.set_xlabel('X (cm)')
        ax.set_ylabel('Y (cm)')
        ax.set_zlabel('Z (cm)')

        # 锁定坐标轴范围
        ax.set_xlim(x_min, x_max)
        ax.set_ylim(y_min, y_max)
        ax.set_zlim(z_min, z_max)

        # 设置观察视角
        ax.view_init(elev=30, azim=45)

        # 保存图片
        safe_time_str = t_str.replace(':', '')
        filename = f"slice_labeled_{safe_time_str}.png"

        plt.savefig(filename, bbox_inches='tight')
        plt.close(fig)

        generated_files.append(filename)
        print(f"  ✅ 已生成: {filename} (包含数值标签)")

    # ==========================================
    # 4. 打包并下载
    # ==========================================
    zip_filename = "grouting_slices_with_labels.zip"
    with zipfile.ZipFile(zip_filename, 'w') as zipf:
        for file in generated_files:
            zipf.write(file)

    print(f"\n🎉 全部处理完成！正在自动下载打包文件: {zip_filename}")
    files.download(zip_filename)

👇 请点击下方按钮上传 Excel/CSV 数据文件 (例如 grouting_final.csv.xlsx)


Saving grouting_final.csv.xlsx to grouting_final.csv (6).xlsx
✅ 文件接收成功: grouting_final.csv (6).xlsx
📍 注浆源点: (100, 50, 20)，起始时间: 10:02:05

⚙️ 开始生成带数值标签的 3D 切片图...
  ✅ 已生成: slice_labeled_100100.png (包含数值标签)
  ✅ 已生成: slice_labeled_100200.png (包含数值标签)
  ✅ 已生成: slice_labeled_100300.png (包含数值标签)
  ✅ 已生成: slice_labeled_100400.png (包含数值标签)
  ✅ 已生成: slice_labeled_100500.png (包含数值标签)
  ✅ 已生成: slice_labeled_100600.png (包含数值标签)
  ✅ 已生成: slice_labeled_100700.png (包含数值标签)
  ✅ 已生成: slice_labeled_100800.png (包含数值标签)
  ✅ 已生成: slice_labeled_100900.png (包含数值标签)
  ✅ 已生成: slice_labeled_101000.png (包含数值标签)
  ✅ 已生成: slice_labeled_101100.png (包含数值标签)
  ✅ 已生成: slice_labeled_101200.png (包含数值标签)

🎉 全部处理完成！正在自动下载打包文件: grouting_slices_with_labels.zip


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [8]:
import pandas as pd
import numpy as np
from google.colab import files

# 1. 上传文件
print("👇 请上传 grouting_final.csv.xlsx")
uploaded = files.upload()
file_name = next(iter(uploaded))

# 2. 计算速度
if file_name.endswith('.csv'):
    df = pd.read_csv(file_name)
else:
    try: df = pd.read_excel(file_name)
    except: df = pd.read_csv(file_name)

df.columns = [c.strip() for c in df.columns]
df['Time_Obj'] = pd.to_datetime(df['Arrival_Time_s'], format='%H:%M:%S', errors='coerce')

# 确定源点
min_idx = df['Time_Obj'].idxmin()
source_row = df.loc[min_idx]
s_time = source_row['Time_Obj']
sx, sy, sz = source_row['X_cm'], source_row['Y_cm'], source_row['Z_cm']

def calc_speed(row):
    if pd.isna(row['Time_Obj']): return 0
    if row.name == min_idx: return -1
    dist = np.sqrt((row['X_cm']-sx)**2 + (row['Y_cm']-sy)**2 + (row['Z_cm']-sz)**2)
    diff = (row['Time_Obj'] - s_time).total_seconds()
    return round(dist / diff, 2) if diff > 0 else 0

df['Speed_cm_s'] = df.apply(calc_speed, axis=1)

# 修正源点速度
max_sp = df[df['Speed_cm_s'] != -1]['Speed_cm_s'].max()
df.loc[df['Speed_cm_s'] == -1, 'Speed_cm_s'] = max_sp

# 3. 导出表格
output_df = df[['Sensor_ID', 'X_cm', 'Y_cm', 'Z_cm', 'Arrival_Time_s', 'Speed_cm_s']]
output_csv = "sensor_speeds_calculated.csv"
output_df.to_csv(output_csv, index=False, encoding='utf-8-sig')

print(f"\n✅ 表格生成完毕！正在下载 {output_csv}")
files.download(output_csv)

👇 请上传 grouting_final.csv.xlsx


Saving grouting_final.csv.xlsx to grouting_final.csv (7).xlsx

✅ 表格生成完毕！正在下载 sensor_speeds_calculated.csv


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>